In [5]:
end_yr = 2100

In [78]:
import os
import logging 
import sys

# Libs
import xarray as xr
import pandas as pd
import numpy as np
import geopandas as gpd
import matplotlib.pyplot as plt

# Locals
import oggm.cfg as cfg

from oggm import utils, workflow, tasks

# only after PR is accepted
from oggm.shop.gcm_climate import process_cmip_data

# Initialize OGGM and set up the default run parameters
cfg.initialize(logging_level='ERROR')
rgi_version = '62'

cfg.PARAMS['border'] = 160 # changed for OGGM v16

cfg.PARAMS['continue_on_error'] = False
cfg.PARAMS['use_multiprocessing']=False
cfg.PARAMS['store_model_geometry'] = True
           

cfg.PATHS['working_dir'] = utils.gettempdir('OGGM_gcm_run', reset=False)


rgi_reg = '17'


# RGI glaciers 
rgi_ids = ['RGI60-01.16122']

# Go - get the pre-processed glacier directories
# TODO -> need to change the preprocessed directory here 
base_url = 'https://cluster.klima.uni-bremen.de/~oggm/gdirs/oggm_v1.6/L3-L5_files/2023.2/elev_bands/W5E5_spinup'
# ole_v2023.1: base_url = 'https://cluster.klima.uni-bremen.de/~oggm/gdirs/oggm_v1.6/L3-L5_files/2023.1/elev_bands/W5E5_spinup'
gdirs = workflow.init_glacier_directories(rgi_ids, from_prepro_level=5, prepro_border=160,
                                          prepro_base_url=base_url, prepro_rgi_version=rgi_version)

ALL_DIAGS = ['volume', 'volume_bsl', 'volume_bwl',
             'area', 'length',  'calving', 'calving_rate',
             'off_area', 'on_area', 'melt_off_glacier',
             'melt_on_glacier', 'liq_prcp_off_glacier', 'liq_prcp_on_glacier',
             'snowfall_off_glacier', 'snowfall_on_glacier', 'model_mb',
             'residual_mb', 'snow_bucket']
# Add debug vars
cfg.PARAMS['store_diagnostic_variables'] = ALL_DIAGS



        
tasks.run_with_hydro(gdir, run_task=tasks.run_from_climate_data,
                     climate_filename='climate_historical',
                     ys=2000, init_model_yr=2000,
                     store_monthly_hydro=True,
                     init_model_filesuffix='_spinup_historical',
                     ref_geometry_filesuffix='_spinup_historical',
                     ref_area_yr = 2000,
                     output_filesuffix='_historical_from_2000_run')

gcms_cmip6 = pd.read_csv('/home/www/oggm/cmip6/all_gcm_list.csv', index_col=0)
# take all gcms (can't say that we only want to process 2000-2100 ....
for gcm in gcms_cmip6.gcm.unique()[:1]: ##TEST:
    df1 = gcms_cmip6.loc[gcms_cmip6.gcm == gcm]
    for ssp in df1.ssp.unique()[:1]:
        df2 = df1.loc[df1.ssp == ssp]
        assert len(df2) == 2
        ft = df2.loc[df2['var'] == 'tas'].iloc[0]
        fp = df2.loc[df2['var'] == 'pr'].iloc[0].path
        rid = ft.fname.replace('_r1i1p1f1_tas.nc', '')
        rid='_CMIP6_' + rid
        ft = ft.path

        process_cmip_data(gdir,filesuffix=rid+'_bc_2000_2019',  # recognize the climate file for later
                                     fpath_temp=ft,  # temperature projections
                                     fpath_precip=fp,  # precip projections
                                     year_range=('2000', '2019'),
                                     #y0=2000-10,y1=2100+10,
                                     );


            
        tasks.run_with_hydro(gdir,
                 run_task=tasks.run_from_climate_data,
                             ys=2020, # this is important! Start from 2020 glacier
                             ye=end_yr,
                 # use gcm_data, not climate_historical
                 climate_filename='gcm_data',
                 # use the chosen scenario
                 climate_input_filesuffix=rid+'_bc_2000_2019',
                 # we start from the previous run, 
                 init_model_filesuffix='_historical_from_2000_run',
                 ref_geometry_filesuffix='_historical_from_2000_run', 
                 ref_area_yr = 2000,
                 # recognize the run for later
                 output_filesuffix=f'_future_run{rid}'+'_bc_2000_2019',
                 # add monthly diagnostics
                 store_monthly_hydro=True);


utils.merge_consecutive_run_outputs(gdir,
                        input_filesuffix_1='_historical_from_2000_run',
                        input_filesuffix_2=f'_future_run{rid}'+'_bc_2000_2019',
                        output_filesuffix=f'_merged_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019',
                        delete_input=False,
                       ) # we will delete that later

2023-05-12 10:09:51: oggm.cfg: Reading default parameters from the OGGM `params.cfg` configuration file.
2023-05-12 10:09:51: oggm.cfg: Multiprocessing switched OFF according to the parameter file.
2023-05-12 10:09:51: oggm.cfg: Multiprocessing: using all available processors (N=32)
2023-05-12 10:09:51: oggm.cfg: PARAMS['border'] changed from `80` to `160`.
2023-05-12 10:09:51: oggm.cfg: PARAMS['store_model_geometry'] changed from `False` to `True`.
2023-05-12 10:09:51: oggm.workflow: init_glacier_directories from prepro level 5 on 1 glaciers.
2023-05-12 10:09:51: oggm.workflow: Execute entity tasks [gdir_from_prepro] on 1 glaciers
2023-05-12 10:09:51: oggm.cfg: PARAMS['store_diagnostic_variables'] changed from `['volume', 'volume_bsl', 'volume_bwl', 'area', 'length', 'calving', 'calving_rate', 'off_area', 'on_area', 'melt_off_glacier', 'melt_on_glacier', 'liq_prcp_off_glacier', 'liq_prcp_on_glacier', 'snowfall_off_glacier', 'snowfall_on_glacier']` to `['volume', 'volume_bsl', 'volume_

InvalidWorkflowError: The two files seem incompatible by data on variable : volume_bwl_m3

In [79]:
df = xr.open_dataset(f'/tmp/OGGM/OGGM_gcm_output/per_glacier/RGI60-01/RGI60-01.16/RGI60-01.16122/model_diagnostics_future_run{rid}'+'_bc_2000_2019.nc')
dh = xr.open_dataset('/tmp/OGGM/OGGM_gcm_output/per_glacier/RGI60-01/RGI60-01.16/RGI60-01.16122/model_diagnostics_historical_from_2000_run.nc')

In [82]:
dh.volume_bwl_m3.sel(time=2020), 


<xarray.DataArray 'volume_bwl_m3' ()>
array(2.916507e+09)
Coordinates:
    time            float64 2.02e+03
    calendar_year   int64 ...
    calendar_month  int64 ...
    hydro_year      int64 ...
    hydro_month     int64 ...
Attributes:
    description:  Glacier volume below water-level
    unit:         m 3

<xarray.DataArray 'volume_bwl_m3' (time: 81)>
array([2.029594e+09, 2.029594e+09, 2.029594e+09, 2.029594e+09, 2.023112e+09,
       2.016336e+09, 2.006386e+09, 2.000814e+09, 1.991653e+09, 1.982263e+09,
       1.970191e+09, 1.960187e+09, 1.948230e+09, 1.935669e+09, 1.917310e+09,
       1.899247e+09, 1.878210e+09, 1.854544e+09, 1.824109e+09, 1.789316e+09,
       1.757660e+09, 1.723041e+09, 1.693973e+09, 1.664198e+09, 1.635968e+09,
       1.602742e+09, 1.572505e+09, 1.531707e+09, 1.496572e+09, 1.452187e+09,
       1.422061e+09, 1.378542e+09, 1.333578e+09, 1.283958e+09, 1.240207e+09,
       1.190983e+09, 1.133951e+09, 1.076799e+09, 1.029195e+09, 9.713440e+08,
       9.143386e+08, 8.624094e+08, 8.184969e+08, 7.859111e+08, 7.563120e+08,
       7.268151e+08, 6.957368e+08, 6.677581e+08, 6.368683e+08, 5.997715e+08,
       5.632919e+08, 5.341504e+08, 5.087423e+08, 4.773650e+08, 4.518088e+08,
       4.196475e+08, 3.797101e+08, 3.481730e+08, 3.160744e+08, 2.739612e+08,
       2.332571e+08, 2.048595e+08, 1.820051e+08, 1.668449e+08, 1.566938e+08,
       1.534813e+08, 1.534813e+08, 1.534813e+08, 1.534813e+08, 1.534813e+08,
       1.534813e+08, 1.534813e+08, 1.534813e+08, 1.534813e+08, 1.534813e+08,
       1.534813e+08, 1.534813e+08, 1.534813e+08, 1.534813e+08, 1.534813e+08,
       1.534813e+08])
Coordinates:
  * time            (time) float64 2.02e+03 2.021e+03 ... 2.099e+03 2.1e+03
    calendar_year   (time) int64 2020 2021 2022 2023 ... 2097 2098 2099 2100
    calendar_month  (time) int64 1 1 1 1 1 1 1 1 1 1 1 ... 1 1 1 1 1 1 1 1 1 1 1
    hydro_year      (time) int64 2020 2021 2022 2023 ... 2097 2098 2099 2100
    hydro_month     (time) int64 4 4 4 4 4 4 4 4 4 4 4 ... 4 4 4 4 4 4 4 4 4 4 4
Attributes:
    description:  Glacier volume below water-level
    unit:         m 3

In [62]:
input_filesuffix_1 = '_historical_from_2000_run'
input_filesuffix_2 = f'_future_run{rid}'+'_bc_2000_2019'

In [69]:
ds1[v].data[-1]

152176563455.63937

In [70]:
ds2[v].data[0]

152176563455.63928

In [72]:
np.allclose(ds1[v].data[-1], ds2[v].data[0])

True

In [63]:
    # Read in the input files and check
    fp1 = gdir.get_filepath('model_diagnostics', filesuffix=input_filesuffix_1)
    with xr.open_dataset(fp1) as ds:
        ds1 = ds.load()
    fp2 = gdir.get_filepath('model_diagnostics', filesuffix=input_filesuffix_2)
    with xr.open_dataset(fp2) as ds:
        ds2 = ds.load()
    if ds1.time[-1] != ds2.time[0]:
        raise InvalidWorkflowError('The two files are incompatible by time')

    # Samity check for all variables as well
    for v in ds1:
        if not np.all(np.isfinite(ds1[v].data[-1])):
            # This is the last year of hydro output - we will discard anyway
            continue
        if np.allclose(ds1[v].data[-1], ds2[v].data[0]):
            # This means that we're OK - the two match
            continue

        # This has to be a bucket of some sort, probably snow or calving
        if len(ds2[v].data.shape) == 1:
            if ds2[v].data[0] != 0:
                raise InvalidWorkflowError('The two files seem incompatible '
                                           f'by data on variable : {v}')
            bucket = ds1[v].data[-1]
        elif len(ds2[v].data.shape) == 2:
            if ds2[v].data[0, 0] != 0:
                raise InvalidWorkflowError('The two files seem incompatible '
                                           f'by data on variable : {v}')
            bucket = ds1[v].data[-1, -1]
        # Carry it to the rest
        ds2[v] = ds2[v] + bucket

    # Merge by removing the last step of file 1 and delete the files if asked
    out_ds = xr.concat([ds1.isel(time=slice(0, -1)), ds2], dim='time')
    if delete_input:
        os.remove(fp1)
        os.remove(fp2)
    # Write out and return
    fp = gdir.get_filepath('model_diagnostics', filesuffix=output_filesuffix)
    out_ds.to_netcdf(fp)
    return out_ds

NameError: name 'InvalidWorkflowError' is not defined

In [68]:
v = 'volume_m3'
if not np.all(np.isfinite(ds1[v].data[-1])):
    # This is the last year of hydro output - we will discard anyway
    continue
if np.allclose(ds1[v].data[-1], ds2[v].data[0]):
    # This means that we're OK - the two match
    continue

SyntaxError: 'continue' not properly in loop (2530398915.py, line 4)

In [ ]:
   for v in ds1:
        if not np.all(np.isfinite(ds1[v].data[-1])):
            # This is the last year of hydro output - we will discard anyway
            continue
        if np.allclose(ds1[v].data[-1], ds2[v].data[0]):
            # This means that we're OK - the two match
            continue

In [66]:
not np.all(np.isfinite(ds1[v].data[-1]))

False

In [65]:
np.allclose(ds1[v].data[-1], ds2[v].data[0])

False

In [64]:
v

'volume_bwl_m3'

In [ ]:
            
# Now comes the actual run
# first using gcm from 2000-end_yr (this is how it is done in Rounce et al., 2023)
workflow.execute_entity_task(run_hydro_from_2000_ref_area_2000_hist_gcm, gdirs, end_yr = end_yr)
# then using W5E5 from 2000-2019, and GCM from 2020-end_yr (this is how it has normally be done in OGGM)
workflow.execute_entity_task(run_hydro_from_2000_ref_area_2000_hist_w5e5, gdirs, end_yr = end_yr)



In [11]:
gdir = gdirs[0]

In [ ]:
ds2[v].data[0] != 0:

In [47]:
dh.volume_bwl_m3.data[0]

2950032038.9243755

In [48]:
df.volume_m3

<xarray.DataArray 'volume_m3' (time: 81)>
array([1.521766e+11, 1.514835e+11, 1.506315e+11, 1.498516e+11, 1.488973e+11,
       1.478050e+11, 1.464810e+11, 1.459238e+11, 1.448239e+11, 1.436834e+11,
       1.427770e+11, 1.425485e+11, 1.419761e+11, 1.412991e+11, 1.400268e+11,
       1.394348e+11, 1.384967e+11, 1.373183e+11, 1.366982e+11, 1.356508e+11,
       1.347067e+11, 1.340160e+11, 1.331507e+11, 1.322606e+11, 1.314263e+11,
       1.307169e+11, 1.300671e+11, 1.293298e+11, 1.286855e+11, 1.273352e+11,
       1.265453e+11, 1.256855e+11, 1.246239e+11, 1.235209e+11, 1.228155e+11,
       1.218040e+11, 1.204660e+11, 1.191776e+11, 1.182569e+11, 1.165477e+11,
       1.154732e+11, 1.143682e+11, 1.134244e+11, 1.127307e+11, 1.117880e+11,
       1.106711e+11, 1.093848e+11, 1.085510e+11, 1.067833e+11, 1.051568e+11,
       1.036594e+11, 1.029821e+11, 1.024501e+11, 1.017731e+11, 1.013637e+11,
       1.004901e+11, 9.944304e+10, 9.807448e+10, 9.707007e+10, 9.621630e+10,
       9.503362e+10, 9.410968e+10, 9.325639e+10, 9.239167e+10, 9.118798e+10,
       8.964416e+10, 8.837261e+10, 8.749102e+10, 8.653839e+10, 8.567434e+10,
       8.448103e+10, 8.337853e+10, 8.197230e+10, 8.068535e+10, 7.907771e+10,
       7.816809e+10, 7.697217e+10, 7.561935e+10, 7.422438e+10, 7.320322e+10,
       7.234413e+10])
Coordinates:
  * time            (time) float64 2.02e+03 2.021e+03 ... 2.099e+03 2.1e+03
    calendar_year   (time) int64 2020 2021 2022 2023 ... 2097 2098 2099 2100
    calendar_month  (time) int64 1 1 1 1 1 1 1 1 1 1 1 ... 1 1 1 1 1 1 1 1 1 1 1
    hydro_year      (time) int64 2020 2021 2022 2023 ... 2097 2098 2099 2100
    hydro_month     (time) int64 4 4 4 4 4 4 4 4 4 4 4 ... 4 4 4 4 4 4 4 4 4 4 4
Attributes:
    description:  Total glacier volume
    unit:         m 3

In [34]:
xr.concat([dh,df], dim='time')

<xarray.Dataset>
Dimensions:                       (time: 102, month_2d: 12)
Coordinates:
  * time                          (time) float64 2e+03 2.001e+03 ... 2.1e+03
    calendar_year                 (time) int64 2000 2001 2002 ... 2098 2099 2100
    calendar_month                (time) int64 1 1 1 1 1 1 1 1 ... 1 1 1 1 1 1 1
    hydro_year                    (time) int64 2000 2001 2002 ... 2098 2099 2100
    hydro_month                   (time) int64 4 4 4 4 4 4 4 4 ... 4 4 4 4 4 4 4
  * month_2d                      (month_2d) int64 1 2 3 4 5 6 7 8 9 10 11 12
    hydro_month_2d                (month_2d) int64 4 5 6 7 8 9 10 11 12 1 2 3
    calendar_month_2d             (month_2d) int64 1 2 3 4 5 6 7 8 9 10 11 12
Data variables: (12/26)
    volume_m3                     (time) float64 1.607e+11 ... 7.234e+10
    volume_bsl_m3                 (time) float64 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0
    volume_bwl_m3                 (time) float64 2.95e+09 2.95e+09 ... 1.535e+08
    area_m2                       (time) float64 4.414e+08 ... 3.965e+08
    length_m                      (time) float64 4.92e+04 4.92e+04 ... 4.12e+04
    calving_m3                    (time) float64 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0
    ...                            ...
    snowfall_on_glacier_monthly   (time, month_2d) float64 1.254e+11 ... nan
    snow_bucket                   (time) float64 0.0 3.616e-05 ... 5.78e+10
    snow_bucket_monthly           (time, month_2d) float64 0.0 4e-06 ... 0.0 0.0
    model_mb                      (time) float64 4.454e+11 -1.153e+11 ... nan
    residual_mb                   (time) float64 -4.101e+09 -4.07e+09 ... nan
    residual_mb_monthly           (time, month_2d) float64 0.0 0.0 ... nan nan
Attributes:
    description:          OGGM model output
    oggm_version:         1.3.2.dev394+gb45b78b
    calendar:             365-day no leap
    creation_date:        2023-05-12 07:34:16
    water_level:          491.3637909324272
    glen_a:               7.830101237437472e-24
    fs:                   0
    mb_model_class:       MultipleFlowlineMassBalance
    mb_model_hemisphere:  nh

In [21]:
gdir.get_filepath('climate_historical')

'/tmp/OGGM/OGGM_gcm_output/per_glacier/RGI60-01/RGI60-01.16/RGI60-01.16122/climate_historical.nc'

In [37]:
utils.merge_consecutive_run_outputs?

Signature:
utils.merge_consecutive_run_outputs(
    gdir,
    input_filesuffix_1=None,
    input_filesuffix_2=None,
    output_filesuffix=None,
    delete_input=False,
)
Docstring:
Merges the output of two model_diagnostics files into one.

It assumes that the last time of file1 is equal to the first time of file2.

Parameters
----------
gdir : the glacier directory
input_filesuffix_1 : str
    how to recognize the first file
input_filesuffix_2 : str
    how to recognize the second file
output_filesuffix : str
    where to write the output (default: no suffix)

Returns
-------
The merged dataset

Notes
-----
Files written to the glacier directory:
File:      ~/.local/lib/python3.10/site-packages/oggm/utils/_workflow.py
Type:      function


In [17]:
m = tasks.run_with_hydro(gdir, run_task=tasks.run_from_climate_data,
                     climate_filename='climate_historical',
                     ys=2000, init_model_yr=2000,
                     store_monthly_hydro=True,
                     init_model_filesuffix='_spinup_historical',
                     ref_geometry_filesuffix='_spinup_historical',
                     ref_area_yr = 2000,
                     output_filesuffix='_historical_from_2000_run')

for gcm in gcms_cmip6.gcm.unique()[:5]: ##TEST:
        df1 = gcms_cmip6.loc[gcms_cmip6.gcm == gcm]
        for ssp in df1.ssp.unique():
            df2 = df1.loc[df1.ssp == ssp]
            assert len(df2) == 2
            ft = df2.loc[df2['var'] == 'tas'].iloc[0]
            rid = ft.fname.replace('_r1i1p1f1_tas.nc', '')
            rid='_CMIP6_' + rid
            
            tasks.run_with_hydro(gdir,
                     run_task=tasks.run_from_climate_data,
                                 ys=2020, # this is important! Start from 2020 glacier
                                 ye=end_yr,
                     # use gcm_data, not climate_historical
                     climate_filename='gcm_data',
                     # use the chosen scenario
                     climate_input_filesuffix=rid+'_bc_2000_2019',
                     # we start from the previous run, 
                     init_model_filesuffix='_historical_from_2000_run',
                     ref_geometry_filesuffix='_historical_from_2000_run', 
                     ref_area_yr = 2000,
                     # recognize the run for later
                     output_filesuffix=f'_future_run{rid}'+'_bc_2000_2019',
                     # add monthly diagnostics
                     store_monthly_hydro=True);
            
            
            utils.merge_consecutive_run_outputs(gdir,
                                    input_filesuffix_1='_historical_from_2000_run',
                                    input_filesuffix_2=f'_future_run{rid}'+'_bc_2000_2019',
                                    output_filesuffix=f'_merged_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019',
                                    delete_input=False,
                                   ) # we will delete that later
            print(gcm)

2023-05-12 09:34:17: oggm.utils: InvalidWorkflowError occurred during task merge_consecutive_run_outputs_merged_from_2000_run_CMIP6_CESM2-WACCM_ssp126_endyr2100_bc_2000_2019 on RGI60-01.16122: The two files seem incompatible by data on variable : volume_bwl_m3


InvalidWorkflowError: The two files seem incompatible by data on variable : volume_bwl_m3

In [8]:
for gcm in gcms_cmip6.gcm.unique(): ##TEST:
    df1 = gcms_cmip6.loc[gcms_cmip6.gcm == gcm]
    for ssp in df1.ssp.unique():
        df2 = df1.loc[df1.ssp == ssp]
        assert len(df2) == 2
        ft = df2.loc[df2['var'] == 'tas'].iloc[0]
        rid = ft.fname.replace('_r1i1p1f1_tas.nc', '')
        rid='_CMIP6_' + rid

        tasks.run_with_hydro(gdir,
                 run_task=tasks.run_from_climate_data,
                             ys=2000, # this is important! Start from 2000 glacier
                             init_model_yr=2000,
                             ye=end_yr,
                 # use gcm_data, not climate_historical
                 climate_filename='gcm_data',
                 # use the chosen scenario
                 climate_input_filesuffix=rid+'_bc_2000_2019',
                 # we start from the previous run, 
                 init_model_filesuffix='_spinup_historical',
                 ref_geometry_filesuffix='_spinup_historical',
                 ref_area_yr = 2000,
                 # recognize the run for later
                 output_filesuffix=f'_gcm_from_2000_run{rid}_endyr{end_yr}'+'_bc_2000_2019',
                 # add monthly diagnostics
                 store_monthly_hydro=True);

        if end_yr != 2300: 
            # only do that for comparison for the common ssps with isimip3b
            if gcm.lower() in ['gfdl-esm4', 'mpi-esm1-2-hr', 'mri-esm2-0']: 
                if ssp in ['ssp126', 'ssp370', 'ssp585']:
                    tasks.run_with_hydro(gdir,
                             run_task=tasks.run_from_climate_data,
                                         ys=2000, # this is important! Start from 2000 glacier
                                         init_model_yr=2000,
                                         ye=end_yr,
                             # use gcm_data, not climate_historical
                             climate_filename='gcm_data',
                             # use the chosen scenario
                             climate_input_filesuffix=rid+'_bc_1979_2014',
                             # we start from the previous run, 
                             init_model_filesuffix='_spinup_historical',
                             ref_geometry_filesuffix='_spinup_historical',
                             ref_area_yr = 2000,
                             # recognize the run for later
                             output_filesuffix=f'_gcm_from_2000_run{rid}_endyr{end_yr}'+'_bc_1979_2014',
                             # add monthly diagnostics
                             store_monthly_hydro=True);

2023-05-12 09:28:13: oggm.core.flowline: FileNotFoundError occurred during task run_from_climate_data_gcm_from_2000_run_CMIP6_MRI-ESM2-0_ssp534-over_endyr2100_bc_2000_2019 on RGI60-01.16122: [Errno 2] No such file or directory: b'/tmp/OGGM/OGGM_gcm_output/per_glacier/RGI60-01/RGI60-01.16/RGI60-01.16122/gcm_data_CMIP6_MRI-ESM2-0_ssp534-over_bc_2000_2019.nc'
2023-05-12 09:28:13: oggm.core.flowline: FileNotFoundError occurred during task run_with_hydro_gcm_from_2000_run_CMIP6_MRI-ESM2-0_ssp534-over_endyr2100_bc_2000_2019 on RGI60-01.16122: [Errno 2] No such file or directory: b'/tmp/OGGM/OGGM_gcm_output/per_glacier/RGI60-01/RGI60-01.16/RGI60-01.16122/gcm_data_CMIP6_MRI-ESM2-0_ssp534-over_bc_2000_2019.nc'


FileNotFoundError: [Errno 2] No such file or directory: b'/tmp/OGGM/OGGM_gcm_output/per_glacier/RGI60-01/RGI60-01.16/RGI60-01.16122/gcm_data_CMIP6_MRI-ESM2-0_ssp534-over_bc_2000_2019.nc'

In [ ]:


# merge data together
if end_yr == 2100:
    for member in isimip3b_members:    
        for ssp in ['ssp126', 'ssp370', 'ssp585']:
            rid = f'_ISIMIP3b_{member}_{ssp}'
            # for W5E5 as past climate 
            utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}', 
                            path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged_endyr2100{rid}_rgi{rgi_reg}_{id0}_{id1}.nc'))
            utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}_bc_2000_2019', 
                            path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged_endyr2100{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))
            
            # for the GCM as past climate 
            utils.compile_run_output(gdirs, input_filesuffix=f'_gcm_from_2000_run{rid}', 
                            path=os.path.join(eq_dir, f'run_hydro_gcm_from_2000_endyr2100{rid}_rgi{rgi_reg}_{id0}_{id1}.nc'))
            utils.compile_run_output(gdirs, input_filesuffix=f'_gcm_from_2000_run{rid}_bc_2000_2019', 
                            path=os.path.join(eq_dir, f'run_hydro_gcm_from_2000_endyr2100{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))


for gcm in gcms_cmip6.gcm.unique(): 
    df1 = gcms_cmip6.loc[gcms_cmip6.gcm == gcm]
    for ssp in df1.ssp.unique():
        df2 = df1.loc[df1.ssp == ssp]
        assert len(df2) == 2
        ft = df2.loc[df2['var'] == 'tas'].iloc[0]
        rid = ft.fname.replace('_r1i1p1f1_tas.nc', '')
        rid='_CMIP6_' + rid

        utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019', 
                                path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged_endyr{end_yr}{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))

        utils.compile_run_output(gdirs, input_filesuffix=f'_gcm_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019', 
                                path=os.path.join(eq_dir, f'run_hydro_gcm_from_2000_endyr{end_yr}{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))
        
        if end_yr == 2100:
            # only do that for comparison for the common ssps with isimip3b
            if gcm.lower() in ['gfdl-esm4', 'mpi-esm1-2-hr', 'mri-esm2-0']: 
                if ssp in ['ssp126', 'ssp370', 'ssp585']:
                    utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}_endyr{end_yr}_bc_1979_2014', 
                                            path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged_endyr{end_yr}{rid}_bc_1979_2014_rgi{rgi_reg}_{id0}_{id1}.nc'))

                    utils.compile_run_output(gdirs, input_filesuffix=f'_gcm_from_2000_run{rid}_endyr{end_yr}_bc_1979_2014', 
                                            path=os.path.join(eq_dir, f'run_hydro_gcm_from_2000_endyr{end_yr}{rid}_bc_1979_2014_rgi{rgi_reg}_{id0}_{id1}.nc'))


    

log.workflow('OGGM Done')